In [1]:
import os
import numpy as np
import pandas as pd

from sklearn.metrics import recall_score, precision_score, roc_curve, roc_auc_score
import scikitplot as skplt

# Plotting
import matplotlib.pyplot as plt
import matplotlib.font_manager as font_manager
import seaborn as sns

# CMS data
from sodapy import Socrata
# https://dev.socrata.com/foundry/data.cms.gov/77gb-8z53

%matplotlib inline
%config InlineBackend.figure_format='retina'
hfont = {'fontname':'Helvetica'}

pd.set_option("max_columns", None)
pd.set_option("max_rows", None)
pd.set_option('display.float_format', lambda x: '%.3f' % x)

import warnings
warnings.filterwarnings('ignore')

In [2]:
### Read in provider speciality mapping file

In [3]:
path_prov_mapping = "/Users/grahambaum/Desktop/FX/Paper_Data/"
df_prov_mapping = pd.read_csv(os.path.join(path_prov_mapping, "CMS Medicare Provider_Supplier Specialty codes.csv"), header=None)
df_prov_mapping = df_prov_mapping.rename(columns={0: "provider_spec_cd", 1: "specialty"})
df_prov_mapping.head()

provider_spec_cd           specialty
0                1    General practice
1                2     General surgery
2                3  Allergy/immunology
3                4      Otolaryngology
4                5      Anesthesiology

In [4]:
### Read in Place of Service Mapping file

In [18]:
path_POS="/Users/grahambaum/Documents/"
df_POS_mapping=pd.read_csv(os.path.join(path_POS, "CMS_Place_of_Service_Codes.csv"))
df_POS_mapping.head()

place_of_service_cd                           PlaceofService_Name  \
0                    1                                      Pharmacy   
1                    2                                    Telehealth   
2                    3                                        School   
3                    4                              Homeless Shelter   
4                    5  Indian Health Service Free-standing Facility   

                          PlaceofService_Description  
0  A facility or location where drugs and other m...  
1  The location where health services and health ...  
2     A facility whose primary purpose is education.  
3  A facility or location whose primary purpose i...  
4  A facility or location, owned and operated by ...

In [6]:
# to understand fields: https://data.cms.gov/Medicare-Physician-Supplier/Medicare-Provider-Utilization-and-Payment-Data-Phy/fs4p-t5eq
client = Socrata("data.cms.gov", None)

In [7]:
# new data: https://www.cms.gov/Research-Statistics-Data-and-Systems/Statistics-Trends-and-Reports/Physician-Supplier-Procedure-Summary
year_phy_supp_db_dict = {2012: "jxyn-53mh",
                         2013: "vvf5-rctb",
                         2014: "rcv5-b2mj",
                         2015: "gwzr-e3a7",
                         2016: "7drh-2rww",
                         2017: "xfvs-efd5",
                         2018: "efgi-jnkv"}

year_phy_supp_treatment_db_dict = {2012: "jxyn-53mh",
                         2013: "vvf5-rctb",
                         2014: "rcv5-b2mj",
                         2015: "gwzr-e3a7",
                         2016: "7drh-2rww",
                         2017: "xfvs-efd5"}

In [8]:
# df_xray_codes_imaging = pd.read_csv("/Users/grahambaum/Downloads/df_xray_codes_all_years_msk_below_neck_no_chest.csv")
df_xray_codes_imaging = pd.read_csv("/Users/grahambaum/Downloads/df_xray_codes_all_years_fx_ifu.csv")

df_xray_codes_imaging["hcpcs_code"] = df_xray_codes_imaging["hcpcs_code"].astype(str)
# Create tuple of cpt codes to query on
df_xray_tuples = tuple(df_xray_codes_imaging["hcpcs_code"])
df_xray_codes_imaging

hcpcs_code                                  hcpcs_description
0       73110                 X-ray of wrist, minimum of 3 views
1       73560                        X-ray of knee, 1 or 2 views
2       73530                        X-ray of hip during surgery
3       73060             X-ray of upper arm, minimum of 2 views
4       73030              X-ray of shoulder, minimum of 2 views
5       72170                      X-ray of pelvis, 1 or 2 views
6       73510                       X-ray of hip 2 or more views
7       73564                     X-ray of knee, 4 or more views
8       73600                            X-ray of ankle, 2 views
9       73610                 X-ray of ankle, minimum of 3 views
10      73550                            X-ray of thigh, 2 views
11      73562                             X-ray of knee, 3 views
12      73500                                 X-ray of hip1 view
13      73590                        X-ray of lower leg, 2 views
14      73565  X-ray of both knees, standing, front to back view
15      73080                 X-ray of elbow, minimum of 3 views
16      73100                            X-ray of wrist, 2 views
17      73070                            X-ray of elbow, 2 views
18      73090                          X-ray of forearm, 2 views
19      73520                       X-ray of hip minimum 2 views
20      72190                X-ray of pelvis, minimum of 3 views
21      72220                X-ray of pelvis, minimum of 2 views
22      73010                            X-ray of shoulder blade
23      73020                          X-ray of shoulder, 1 view
24      72200      X-ray of sacroiliac joints, less than 3 views
25      73525                                 X-ray of hip joint
26      72202        X-ray of sacroiliac joints, 3 or more views
27      73000                               X-ray of collar bone
28      73580                                X-ray of knee joint
29      73050                               X-ray of collar bone
30      77074                                     X-ray of bones
31      73540  X-ray of pelvis and hips, infant or child, min...
32      73615                               X-ray of ankle joint
33      73085  Radiological supervision and interpretation X-...
34      73500                               X-ray of hip, 1 view
35      73520                 X-ray of both hips minimum 2 views
36      73500           X-ray of hip on one side of body, 1 view
37      73525  Radiological supervision and interpretation X-...
38      73580  Radiological supervision and interpretation X-...
39      73050                         X-ray of both collar bones
40      73615  Radiological supervision and interpretation X-...
41      73502                X-ray of hip with pelvis, 2-3 views
42      73501                   X-ray of hip with pelvis, 1 view
43      73552                    X-ray of femur, minimum 2 views
44      73551                             X-ray of femur, 1 view
45      73522          X-ray of both hips with pelvis, 3-4 views
46      73523  X-ray of both hips with pelvis, minimum of 5 v...
47      73521            X-ray of both hips with pelvis, 2 views
48      73503       X-ray of hip with pelvis, minimum of 4 views

In [9]:
###############################
## GROUP BY PLACE OF SERVICE ##
###############################
# Adding limit into the query or else it seems to default to 1000 rows and we would be missing data
limit_rows = 10000000
df_imaging_total_volume_POS = pd.DataFrame()

for year in year_phy_supp_db_dict.keys():
    print(year)
    results_imaging_xray_volume = client.get(year_phy_supp_db_dict[year], where=f"hcpcs_cd IN {df_xray_tuples}",
                                 limit=limit_rows)

    df_imaging_xray_volume_POS = pd.DataFrame.from_records(results_imaging_xray_volume)
    # Transform types
    df_imaging_xray_volume_POS["psps_submitted_service_cnt"] = pd.to_numeric(df_imaging_xray_volume_POS["psps_submitted_service_cnt"])
    df_imaging_xray_volume_POS["psps_nch_payment_amt"] = pd.to_numeric(df_imaging_xray_volume_POS["psps_nch_payment_amt"])

    ## EXCLUDE TECHNICAL COMPONENT CLAIMS (as in Mizrahi 2017)
    df_imaging_xray_volume_POS=df_imaging_xray_volume_POS.loc[df_imaging_xray_volume_POS['hcpcs_initial_modifier_cd']!='TC']
    
    # Group by POS code and provider type
    df_imaging_xray_volume_POS_gr = df_imaging_xray_volume_POS.groupby(["provider_spec_cd", "place_of_service_cd"], 
                                                          as_index=False)["psps_submitted_service_cnt",
                                                                         "psps_nch_payment_amt"].sum()
    df_imaging_xray_volume_POS_gr["year"] = year

    # Concatenate over the years
    df_imaging_total_volume_POS = pd.concat([df_imaging_total_volume_POS, df_imaging_xray_volume_POS_gr])
    
    # check if limit rows is maxed out- if so you need to increase
    if limit_rows == len(df_imaging_xray_volume_POS):
        print("INCREASE LIMIT ROWS VARIABLE - QUERY MAXED OUT")

2012
2013
2014
2015
2016
2017
2018


In [10]:
#######################################################
### Calculate total volume for each setting in 2018 ###
#######################################################

df_imaging_total_volume_POS["place_of_service_cd"]=pd.to_numeric(df_imaging_total_volume_POS["place_of_service_cd"])




df_imaging_total_volume_POS_2018= df_imaging_total_volume_POS.loc[df_imaging_total_volume_POS['year']==2018]

df_imaging_total_volume_POS_2018_gr = df_imaging_total_volume_POS_2018.groupby(["place_of_service_cd"], as_index=False)["psps_submitted_service_cnt"].sum()




total_df = df_imaging_total_volume_POS_2018_gr.loc[df_imaging_total_volume_POS_2018_gr['place_of_service_cd'].isin([11,19, 20, 21, 22, 23])]
df_imaging_total_volume_POS_2018_gr

total_df

office_total=total_df.loc[total_df["place_of_service_cd"]==11]
office_total=np.sum(office_total['psps_submitted_service_cnt'])

inpatient_total=total_df.loc[total_df["place_of_service_cd"]==21]
inpatient_total=np.sum(inpatient_total['psps_submitted_service_cnt'])

emergency_total=total_df.loc[total_df["place_of_service_cd"]==23]
emergency_total= np.sum(emergency_total['psps_submitted_service_cnt'])

urgent_total=total_df.loc[total_df["place_of_service_cd"]==20]
urgent_total= np.sum(urgent_total['psps_submitted_service_cnt'])

outpatient_total=total_df.loc[total_df["place_of_service_cd"].isin([19,22])]
outpatient_total = np.sum(outpatient_total['psps_submitted_service_cnt'])

all_hospital_total= inpatient_total + emergency_total + outpatient_total

all_hospital_total

# office_total['psps_submitted_service_cnt']
# total_df


# Office
# df_imaging_total_volume_POS_2018_office= df_imaging_total_volume_POS_2018.loc[df_imaging_total_volume_POS_2018['place_of_service_cd']==11]

# df_imaging_total_volume_POS_2018_office


8811194.0

In [ ]:
## Read in CSV file to avoid running the query
# df_imaging_total_volume_POS=pd.read_csv("/Users/grahambaum/Desktop/FX/Paper_Data/df_imaging_total_volume_noChest_POS.csv")
df_imaging_total_volume_POS.head(10)

In [12]:
##################################
## Merge in provider speciality ##
##################################
df_imaging_total_volume_POS_prov = df_imaging_total_volume_POS.merge(df_prov_mapping, on = "provider_spec_cd", how="inner")
# df_imaging_total_volume_prov.to_csv("/Users/grahambaum/Desktop/FX/Paper_Data/df_imaging_total_volume_prov_no_chest.csv", index=False)

df_imaging_total_volume_POS_prov.head()

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
0               10                   11                     369.000   
1               10                   11                     228.000   
2               10                   22                       0.000   
3               10                   11                      87.000   
4               10                   20                       0.000   

   psps_nch_payment_amt  year         specialty  
0             17707.650  2012  Gastroenterology  
1             12863.550  2013  Gastroenterology  
2                 8.570  2013  Gastroenterology  
3              8581.550  2014  Gastroenterology  
4               557.760  2014  Gastroenterology

In [ ]:
df_imaging_total_volume_POS_prov

In [19]:
df_imaging_total_volume_POS_prov["place_of_service_cd"]=pd.to_numeric(df_imaging_total_volume_POS_prov["place_of_service_cd"])
df_POS_mapping['place_of_service_cd']=pd.to_numeric(df_POS_mapping['place_of_service_cd'])

In [20]:
## Merge with Place of Service (POS) Codes
df_imaging_total_volume_POS_prov_pos = df_imaging_total_volume_POS_prov.merge(df_POS_mapping, on = "place_of_service_cd", how="inner")
df_imaging_total_volume_POS_prov_pos.head()

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
0               10                   11                     369.000   
1               10                   11                     228.000   
2               10                   11                      87.000   
3               10                   11                     100.000   
4               10                   11                     136.000   

   psps_nch_payment_amt  year         specialty PlaceofService_Name  \
0             17707.650  2012  Gastroenterology              Office   
1             12863.550  2013  Gastroenterology              Office   
2              8581.550  2014  Gastroenterology              Office   
3              7804.470  2015  Gastroenterology              Office   
4              8492.230  2016  Gastroenterology              Office   

                          PlaceofService_Description  
0  Location, other than a hospital, skilled nursi...  
1  Location, other than a hospital, skilled nursi...  
2  Location, other than a hospital, skilled nursi...  
3  Location, other than a hospital, skilled nursi...  
4  Location, other than a hospital, skilled nursi...

In [33]:
df_imaging_total_volume_POS_prov_pos.to_csv("/Users/grahambaum/Desktop/FX/Paper_Data/df_imaging_total_volume_POS_prov_FX_ifu_TC_excl.csv", index=False)

In [ ]:
## Read in CSV file to avoid running the query
# df_imaging_total_volume_POS_prov_pos = pd.read_csv("/Users/grahambaum/Desktop/FX/Paper_Data/df_imaging_total_volume_noChest_POS_prov_pos.csv")
# df_imaging_total_volume_POS_prov_pos = pd.read_csv("/Users/grahambaum/Desktop/FX/Paper_Data/df_imaging_total_volume_POS_prov_FX_ifu.csv")
# df_imaging_total_volume_POS_prov_pos.head()

In [ ]:
## Add "Non-physician" label
# nonphysician_list = ["Nurse practitioner", "Physician assistant"]#, "Chiropractic"]

# Non-physicians
# df_imaging_total_volume_POS_prov_rename_non_phy = df_imaging_total_volume_POS_prov_pos.copy()
# for spec in nonphysician_list:
#     df_imaging_total_volume_POS_prov_rename_non_phy.replace(spec, "Non-Physician", inplace=True)


In [21]:
## Add "Primary Care"
primary_care_list = ["Internal medicine", "Family practice"] # ,"] #, "Osteopathic manipulative medicine","Hospice and palliative care"]

# Primary Care
df_imaging_total_volume_POS_prov_rename_pcp = df_imaging_total_volume_POS_prov_pos.copy()
for spec in primary_care_list:
    df_imaging_total_volume_POS_prov_pos.replace(spec, "Primary Care", inplace=True)

In [22]:
### Breakdown of POS by Provider Type

In [23]:
## Radiologists
df_rads = df_imaging_total_volume_POS_prov_pos.loc[df_imaging_total_volume_POS_prov_pos["specialty"]=="Diagnostic radiology"]
df_rads.sort_values(by="psps_submitted_service_cnt", ascending=False, inplace=True)

df_rads = df_rads.sort_values(["year","psps_submitted_service_cnt"], ascending=(True, False))

In [24]:
df_rads_groupby_Year = df_rads.groupby(["year", "place_of_service_cd"], as_index=False)["psps_submitted_service_cnt"].sum()
df_rads_groupby_Year

year  place_of_service_cd  psps_submitted_service_cnt
0    2012                    1                       0.000
1    2012                    3                       0.000
2    2012                    4                       0.000
3    2012                    9                       0.000
4    2012                   11                 1525978.000
5    2012                   12                    1799.000
6    2012                   13                     104.000
7    2012                   14                       0.000
8    2012                   15                      12.000
9    2012                   20                   10109.000
10   2012                   21                 2059037.200
11   2012                   22                 3241812.100
12   2012                   23                 2907775.200
13   2012                   24                      59.000
14   2012                   25                       0.000
15   2012                   26                       0.000
16   2012                   31                    2794.000
17   2012                   32                   27181.000
18   2012                   33                       0.000
19   2012                   41                       0.000
20   2012                   49                   10618.000
21   2012                   50                       0.000
22   2012                   51                       0.000
23   2012                   53                       0.000
24   2012                   54                      28.000
25   2012                   55                       0.000
26   2012                   56                       0.000
27   2012                   61                      11.000
28   2012                   62                       0.000
29   2012                   71                      12.000
30   2012                   72                     194.000
31   2012                   81                      73.000
32   2012                   99                    3273.000
33   2013                    1                       0.000
34   2013                    3                       0.000
35   2013                    4                       0.000
36   2013                    6                       0.000
37   2013                    7                       0.000
38   2013                    9                       0.000
39   2013                   11                 1493984.100
40   2013                   12                    7604.000
41   2013                   13                    1083.000
42   2013                   14                       0.000
43   2013                   15                     619.000
44   2013                   16                       0.000
45   2013                   20                   11602.000
46   2013                   21                 1990468.600
47   2013                   22                 3316591.400
48   2013                   23                 3015291.000
49   2013                   24                     131.000
50   2013                   25                       0.000
51   2013                   26                       0.000
52   2013                   31                    6429.000
53   2013                   32                   34052.000
54   2013                   33                    1414.000
55   2013                   34                       0.000
56   2013                   49                   12615.000
57   2013                   50                       0.000
58   2013                   51                      17.000
59   2013                   53                       0.000
60   2013                   54                       0.000
61   2013                   56                       0.000
62   2013                   61                     221.000
63   2013                   62                       0.000
64   2013                   71                       0.000
65   2013                   72                     803.000
66   2013                   81                      

In [25]:
## 2018 - Radiologists
df_rads_groupby_Year_2018 = df_rads_groupby_Year.loc[df_rads_groupby_Year["year"]==2018]
df_rads_groupby_Year_2018.sort_values(by="psps_submitted_service_cnt", ascending=False, inplace=True)
df_rads_groupby_Year_2018.head(10)

year  place_of_service_cd  psps_submitted_service_cnt
222  2018                   23                 3276766.000
221  2018                   22                 2993915.000
213  2018                   11                 1610706.000
220  2018                   21                 1605976.000
218  2018                   19                  458555.000
226  2018                   32                   68907.000
219  2018                   20                   32150.000
225  2018                   31                   31651.000
229  2018                   49                   15838.000
215  2018                   13                   10579.000

In [26]:
## Ortho
df_ortho = df_imaging_total_volume_POS_prov_pos.loc[df_imaging_total_volume_POS_prov_pos["specialty"]=="Orthopedic surgery"]
df_ortho.sort_values(by="psps_submitted_service_cnt", ascending=False, inplace=True)
df_ortho.head(10)

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
60                20                   11                 6099182.300   
61                20                   11                 6057557.100   
58                20                   11                 6053522.200   
59                20                   11                 6051871.900   
62                20                   11                 5656386.900   
63                20                   11                 5505722.300   
64                20                   11                 5409958.500   
486               20                   22                  207410.000   
487               20                   22                  207224.000   
485               20                   22                  177876.000   

     psps_nch_payment_amt  year           specialty  \
60          138743246.860  2014  Orthopedic surgery   
61          127819482.810  2015  Orthopedic surgery   
58          139789936.900  2012  Orthopedic surgery   
59          142151817.590  2013  Orthopedic surgery   
62          126591017.670  2016  Orthopedic surgery   
63          124888873.340  2017  Orthopedic surgery   
64          123967308.890  2018  Orthopedic surgery   
486           1566231.510  2014  Orthopedic surgery   
487           1524174.480  2015  Orthopedic surgery   
485           1290708.620  2013  Orthopedic surgery   

               PlaceofService_Name  \
60                          Office   
61                          Office   
58                          Office   
59                          Office   
62                          Office   
63                          Office   
64                          Office   
486  On Campus-Outpatient Hospital   
487  On Campus-Outpatient Hospital   
485  On Campus-Outpatient Hospital   

                            PlaceofService_Description  
60   Location, other than a hospital, skilled nursi...  
61   Location, other than a hospital, skilled nursi...  
58   Location, other than a hospital, skilled nursi...  
59   Location, other than a hospital, skilled nursi...  
62   Location, other than a hospital, skilled nursi...  
63   Location, other than a hospital, skilled nursi...  
64   Location, other than a hospital, skilled nursi...  
486  A portion of a hospital which provides diagnos...  
487  A portion of a hospital which provides diagnos...  
485  A portion of a hospital which provides diagnos...

In [27]:
## Physician Assistant
df_pa = df_imaging_total_volume_POS_prov.loc[df_imaging_total_volume_POS_prov["specialty"]=="Physician assistant"]
df_pa = df_pa.sort_values(["year","psps_submitted_service_cnt"], ascending=(True, False))
df_pa.head(20)

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
3097               97                   11                  396196.000   
3102               97                   22                   19055.000   
3100               97                   20                    5226.000   
3103               97                   23                    4785.000   
3101               97                   21                      59.000   
3105               97                   31                      37.000   
3093               97                    1                       0.000   
3094               97                    3                       0.000   
3095               97                    7                       0.000   
3096               97                    9                       0.000   
3098               97                   12                       0.000   
3099               97                   17                       0.000   
3104               97                   24                       0.000   
3106               97                   32                       0.000   
3107               97                   50                       0.000   
3108               97                   57                       0.000   
3109               97                   61                       0.000   
3110               97                   71                       0.000   
3111               97                   72                       0.000   
3112               97                   99                       0.000   

      psps_nch_payment_amt  year            specialty  
3097           7435304.210  2012  Physician assistant  
3102            132060.340  2012  Physician assistant  
3100            158367.350  2012  Physician assistant  
3103             28222.310  2012  Physician assistant  
3101              1078.290  2012  Physician assistant  
3105               831.740  2012  Physician assistant  
3093                 0.000  2012  Physician assistant  
3094                47.520  2012  Physician assistant  
3095                 0.000  2012  Physician assistant  
3096                18.550  2012  Physician assistant  
3098               522.900  2012  Physician assistant  
3099                22.120  2012  Physician assistant  
3104                61.290  2012  Physician assistant  
3106                 6.050  2012  Physician assistant  
3107                51.030  2012  Physician assistant  
3108                 0.000  2012  Physician assistant  
3109                 6.980  2012  Physician assistant  
3110                88.340  2012  Physician assistant  
3111                90.230  2012  Physician assistant  
3112                16.680  2012  Physician assistant

In [28]:
## 2018- PAs
df_pa_groupby_Year_2018 = df_pa.loc[df_pa["year"]==2018]
df_pa_groupby_Year_2018.sort_values(by="psps_submitted_service_cnt", ascending=False, inplace=True)
df_pa_groupby_Year_2018.head(10)

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
3230               97                   11                  764125.000   
3236               97                   20                   28768.000   
3238               97                   22                   27201.000   
3235               97                   19                   11901.000   
3239               97                   23                    4246.000   
3244               97                   49                      88.000   
3241               97                   31                      43.000   
3233               97                   15                      24.000   
3234               97                   16                      19.000   
3237               97                   21                      12.000   

      psps_nch_payment_amt  year            specialty  
3230          13158638.270  2018  Physician assistant  
3236            491371.230  2018  Physician assistant  
3238            180290.570  2018  Physician assistant  
3235             84031.220  2018  Physician assistant  
3239             29247.680  2018  Physician assistant  
3244              3582.370  2018  Physician assistant  
3241              2659.840  2018  Physician assistant  
3233              1884.020  2018  Physician assistant  
3234               342.080  2018  Physician assistant  
3237               995.440  2018  Physician assistant

In [29]:
## Primary Care
df_pcp = df_imaging_total_volume_POS_prov_pos[df_imaging_total_volume_POS_prov_pos["specialty"]=="Primary Care"]
df_pcp.sort_values(by="psps_submitted_service_cnt", ascending=False, inplace=True)
df_pcp.head(10)

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
7                 11                   11                  154484.000   
8                 11                   11                  145396.000   
9                 11                   11                  138961.000   
10                11                   11                  124182.000   
11                11                   11                  119723.000   
12                11                   11                  106478.000   
13                11                   11                   93496.000   
780               11                   20                    6234.000   
779               11                   20                    6079.000   
778               11                   20                    5698.000   

     psps_nch_payment_amt  year     specialty   PlaceofService_Name  \
7             4080323.710  2012  Primary Care                Office   
8             3889799.540  2013  Primary Care                Office   
9             3552707.770  2014  Primary Care                Office   
10            2922583.060  2015  Primary Care                Office   
11            3194024.040  2016  Primary Care                Office   
12            2957959.820  2017  Primary Care                Office   
13            2664076.480  2018  Primary Care                Office   
780            234860.270  2017  Primary Care  Urgent Care Facility   
779            223549.660  2016  Primary Care  Urgent Care Facility   
778            196096.920  2015  Primary Care  Urgent Care Facility   

                            PlaceofService_Description  
7    Location, other than a hospital, skilled nursi...  
8    Location, other than a hospital, skilled nursi...  
9    Location, other than a hospital, skilled nursi...  
10   Location, other than a hospital, skilled nursi...  
11   Location, other than a hospital, skilled nursi...  
12   Location, other than a hospital, skilled nursi...  
13   Location, other than a hospital, skilled nursi...  
780  Location, distinct from a hospital emergency r...  
779  Location, distinct from a hospital emergency r...  
778  Location, distinct from a hospital emergency r...

In [30]:
## 2018- Primary Care
df_pcp_groupby_Year_2018 = df_pcp.loc[df_pcp["year"]==2018]
df_pcp_groupby_Year_2018.sort_values(by="psps_submitted_service_cnt", ascending=False, inplace=True)
df_pcp_groupby_Year_2018.head(10)

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
13                 11                   11                   93496.000   
781                11                   20                    5470.000   
1811               11                   19                     912.000   
1306               11                   23                     783.000   
448                11                   22                     349.000   
1558               11                   21                      94.000   
2209               11                   13                      12.000   
2068               11                   12                       0.000   
2309               11                   26                       0.000   
2336               11                   31                       0.000   

      psps_nch_payment_amt  year     specialty  \
13             2664076.480  2018  Primary Care   
781             225626.390  2018  Primary Care   
1811              9715.780  2018  Primary Care   
1306             15326.860  2018  Primary Care   
448               9233.550  2018  Primary Care   
1558              3690.710  2018  Primary Care   
2209               255.090  2018  Primary Care   
2068               199.040  2018  Primary Care   
2309                 0.000  2018  Primary Care   
2336               175.430  2018  Primary Care   

                 PlaceofService_Name  \
13                            Office   
781             Urgent Care Facility   
1811  Off Campus-Outpatient Hospital   
1306       Emergency Room - Hospital   
448    On Campus-Outpatient Hospital   
1558              Inpatient Hospital   
2209        Assisted Living Facility   
2068                            Home   
2309     Military Treatment Facility   
2336        Skilled Nursing Facility   

                             PlaceofService_Description  
13    Location, other than a hospital, skilled nursi...  
781   Location, distinct from a hospital emergency r...  
1811  A portion of an off-campus hospital provider b...  
1306  A portion of a hospital where emergency diagno...  
448   A portion of a hospital which provides diagnos...  
1558  A facility, other than psychiatric, which prim...  
2209  Congregate residential facility with self-cont...  
2068  Location, other than a hospital or other facil...  
2309  A medical facility operated by one or more of ...  
2336  A facility which primarily provides inpatient ...

In [31]:
## Emergency
df_emergency = df_imaging_total_volume_POS_prov_pos.loc[df_imaging_total_volume_POS_prov_pos["specialty"]=="Emergency medicine"]
df_emergency.sort_values(by="psps_submitted_service_cnt", ascending=False, inplace=True)
df_emergency.head(10)

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
1512               93                   23                   58107.000   
1513               93                   23                   56556.000   
1514               93                   23                   54405.000   
1515               93                   23                   47701.000   
1517               93                   23                   40815.000   
1516               93                   23                   40693.500   
1518               93                   23                   38200.000   
373                93                   11                   31634.000   
374                93                   11                   30053.000   
371                93                   11                   29554.000   

      psps_nch_payment_amt  year           specialty  \
1512            355348.180  2012  Emergency medicine   
1513            338119.830  2013  Emergency medicine   
1514            365648.180  2014  Emergency medicine   
1515            317982.090  2015  Emergency medicine   
1517            318775.610  2017  Emergency medicine   
1516            273942.580  2016  Emergency medicine   
1518            287997.250  2018  Emergency medicine   
373             955118.280  2014  Emergency medicine   
374             835514.060  2015  Emergency medicine   
371             888763.120  2012  Emergency medicine   

            PlaceofService_Name  \
1512  Emergency Room - Hospital   
1513  Emergency Room - Hospital   
1514  Emergency Room - Hospital   
1515  Emergency Room - Hospital   
1517  Emergency Room - Hospital   
1516  Emergency Room - Hospital   
1518  Emergency Room - Hospital   
373                      Office   
374                      Office   
371                      Office   

                             PlaceofService_Description  
1512  A portion of a hospital where emergency diagno...  
1513  A portion of a hospital where emergency diagno...  
1514  A portion of a hospital where emergency diagno...  
1515  A portion of a hospital where emergency diagno...  
1517  A portion of a hospital where emergency diagno...  
1516  A portion of a hospital where emergency diagno...  
1518  A portion of a hospital where emergency diagno...  
373   Location, other than a hospital, skilled nursi...  
374   Location, other than a hospital, skilled nursi...  
371   Location, other than a hospital, skilled nursi...

In [32]:
### Place of Service Breakdown by Provider Type

In [34]:
## Read in CSV file to avoid running the CMS query
# df_imaging_total_volume_POS_prov_pos = pd.read_csv("/Users/grahambaum/Desktop/FX/Paper_Data/df_imaging_total_volume_noChest_POS_prov_pos.csv")
# df_imaging_total_volume_POS_prov_pos = pd.read_csv("/Users/grahambaum/Desktop/FX/Paper_Data/df_imaging_total_volume_POS_prov_FX_ifu_TC_excl.csv")

df_imaging_total_volume_POS_prov_pos.head()

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
0               10                   11                     369.000   
1               10                   11                     228.000   
2               10                   11                      87.000   
3               10                   11                     100.000   
4               10                   11                     136.000   

   psps_nch_payment_amt  year         specialty PlaceofService_Name  \
0             17707.650  2012  Gastroenterology              Office   
1             12863.550  2013  Gastroenterology              Office   
2              8581.550  2014  Gastroenterology              Office   
3              7804.470  2015  Gastroenterology              Office   
4              8492.230  2016  Gastroenterology              Office   

                          PlaceofService_Description  
0  Location, other than a hospital, skilled nursi...  
1  Location, other than a hospital, skilled nursi...  
2  Location, other than a hospital, skilled nursi...  
3  Location, other than a hospital, skilled nursi...  
4  Location, other than a hospital, skilled nursi...

In [35]:
## Read in number of medicare enrollees (to calculate utilization rates)
df_medicare_enrollment = pd.read_csv("/Users/grahambaum/Documents/Medicare_Enrollment_2012to2018.csv")

df_medicare_enrollment.head(10)


year  Total_Original_Medicare_Enrollment
0  2012                            37213622
1  2013                            37613096
2  2014                            37790373
3  2015                            38025274
4  2016                            38610384
5  2017                            38667830
6  2018                            38665082

In [ ]:
## Merge in Medicare Enrollment
# df_imaging_total_volume_POS_prov_pos = df_imaging_total_volume_POS_prov_pos.merge(df_medicare_enrollment, on = "year", how="inner")
# df_imaging_total_volume_POS_prov_pos.head()

In [36]:
## Group off-campus and on-campus outpatient hospitals
outpatient_hospital_list=["Off Campus-Outpatient Hospital", "On Campus-Outpatient Hospital"]


df_imaging_total_volume_POS_prov_pos_rename_HOPD = df_imaging_total_volume_POS_prov_pos.copy()

for pos in outpatient_hospital_list:
    df_imaging_total_volume_POS_prov_pos_rename_HOPD.replace(pos, "HOPD", inplace=True)
df_imaging_total_volume_POS_prov_pos_rename_HOPD

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
0                  10                   11                     369.000   
1                  10                   11                     228.000   
2                  10                   11                      87.000   
3                  10                   11                     100.000   
4                  10                   11                     136.000   
5                  10                   11                      76.000   
6                  10                   11                      50.000   
7                  11                   11                  154484.000   
8                  11                   11                  145396.000   
9                  11                   11                  138961.000   
10                 11                   11                  124182.000   
11                 11                   11                  119723.000   
12                 11                   11                  106478.000   
13                 11                   11                   93496.000   
14                 12                   11                    5451.000   
15                 12                   11                    3376.000   
16                 12                   11                    4682.000   
17                 12                   11                    5034.000   
18                 12                   11                    6563.000   
19                 12                   11                    6598.000   
20                 12                   11                    6646.000   
21                 13                   11                     164.000   
22                 13                   11                     360.000   
23                 13                   11                     908.000   
24                 13                   11                     463.000   
25                 13                   11                     511.000   
26                 13                   11                     430.000   
27                 13                   11                     993.000   
28                 14                   11                     809.000   
29                 14                   11                    1070.000   
30                 14                   11                    1446.000   
31                 14                   11                    1291.000   
32                 14                   11                    1708.000   
33                 14                   11                    1516.000   
34                 14                   11                    1879.000   
35                 16                   11                    3024.000   
36                 16                   11                    1774.000   
37                 16                   11                    3354.000   
38                 16                   11                    3825.000   
39                 16                   11                    2098.000   
40                 16                   11                    1750.000   
41                 16                   11                    1465.000   
42                 17                   11                       0.000   
43                 17                   11                       0.000   
44                 17                   11                       0.000   
45                 17                   11                       0.000   
46                 17                   11                       0.000   
47                 17                   11                       0.000   
48                 18                   11                     421.000   
49                 18                   11                     448.000   
50                 18                   11                     169.000   
51                 18                   11                      86.000   
52                 18                   11                     117.000   
53       

In [37]:
## Group all hospitals (as in Mizrahi et al., 2017)
all_hospital_list=["Off Campus-Outpatient Hospital", "On Campus-Outpatient Hospital", "Inpatient Hospital", "Emergency Room - Hospital"]

df_imaging_total_volume_POS_prov_pos_rename_total_hospital = df_imaging_total_volume_POS_prov_pos.copy()

for pos in all_hospital_list:
    df_imaging_total_volume_POS_prov_pos_rename_total_hospital.replace(pos, "Total Hospital", inplace=True)

df_imaging_total_volume_POS_prov_pos_rename_total_hospital

provider_spec_cd  place_of_service_cd  psps_submitted_service_cnt  \
0                  10                   11                     369.000   
1                  10                   11                     228.000   
2                  10                   11                      87.000   
3                  10                   11                     100.000   
4                  10                   11                     136.000   
5                  10                   11                      76.000   
6                  10                   11                      50.000   
7                  11                   11                  154484.000   
8                  11                   11                  145396.000   
9                  11                   11                  138961.000   
10                 11                   11                  124182.000   
11                 11                   11                  119723.000   
12                 11                   11                  106478.000   
13                 11                   11                   93496.000   
14                 12                   11                    5451.000   
15                 12                   11                    3376.000   
16                 12                   11                    4682.000   
17                 12                   11                    5034.000   
18                 12                   11                    6563.000   
19                 12                   11                    6598.000   
20                 12                   11                    6646.000   
21                 13                   11                     164.000   
22                 13                   11                     360.000   
23                 13                   11                     908.000   
24                 13                   11                     463.000   
25                 13                   11                     511.000   
26                 13                   11                     430.000   
27                 13                   11                     993.000   
28                 14                   11                     809.000   
29                 14                   11                    1070.000   
30                 14                   11                    1446.000   
31                 14                   11                    1291.000   
32                 14                   11                    1708.000   
33                 14                   11                    1516.000   
34                 14                   11                    1879.000   
35                 16                   11                    3024.000   
36                 16                   11                    1774.000   
37                 16                   11                    3354.000   
38                 16                   11                    3825.000   
39                 16                   11                    2098.000   
40                 16                   11                    1750.000   
41                 16                   11                    1465.000   
42                 17                   11                       0.000   
43                 17                   11                       0.000   
44                 17                   11                       0.000   
45                 17                   11                       0.000   
46                 17                   11                       0.000   
47                 17                   11                       0.000   
48                 18                   11                     421.000   
49                 18                   11                     448.000   
50                 18                   11                     169.000   
51                 18                   11                      86.000   
52                 18                   11                     117.000   
53       

In [38]:
## Function for percent change in utilization for each place of service
def perc_change(df, pos_list, base_year):
    df_group = df.loc[df["PlaceofService_Name"].isin(pos_list)]
    df_group.reset_index(drop=True, inplace=True)
    df_group.sort_values(by="year", inplace=True)
    val_base = float(df_group.loc[df_group["year"] == base_year]["utilization"])
    df_group["% change y/o/y"] = 100*df_group["utilization"].pct_change()
    df_group["% change"] = None
    for i in range(len(df_group)):
        df_group["% change"].iloc[i] = 100 * (df_group["utilization"].iloc[i] - val_base)/val_base
    
    return df_group

In [ ]:
## Re-label "Non-Physician" group (Nurse Practitioner + PAs)
# Non-physicians
# df_imaging_total_volume_POS_prov_pos_rename_pa = df_imaging_total_volume_POS_prov_pos.copy()

# for spec in pa_list:
#     df_imaging_total_volume_POS_prov_pos_rename_pa.replace(spec, "Physician Assistant", inplace=True)

    
# df_imaging_total_volume_POS_prov_pos = df_imaging_total_volume_POS_prov_pos_rename_nonPhys

In [39]:
# df_imaging_total_volume_POS_prov_pos=df_imaging_total_volume_POS_prov_pos_rename_total_hospital

df_imaging_total_volume_POS_prov_pos["place_of_service_cd"]=pd.to_numeric(df_imaging_total_volume_POS_prov_pos["place_of_service_cd"])


## Emergency Room Hospital
df_ER = df_imaging_total_volume_POS_prov_pos.loc[df_imaging_total_volume_POS_prov_pos["place_of_service_cd"]==23]

## Inpatient
df_inpatient = df_imaging_total_volume_POS_prov_pos.loc[df_imaging_total_volume_POS_prov_pos["place_of_service_cd"]==21]

## Outpatient Hospital
df_HOPD = df_imaging_total_volume_POS_prov_pos_rename_HOPD.loc[df_imaging_total_volume_POS_prov_pos_rename_HOPD["PlaceofService_Name"]=="HOPD"]

## Office
df_office = df_imaging_total_volume_POS_prov_pos.loc[df_imaging_total_volume_POS_prov_pos["place_of_service_cd"]==11]

## Urgent Care
df_urgent = df_imaging_total_volume_POS_prov_pos.loc[df_imaging_total_volume_POS_prov_pos["place_of_service_cd"]==20]

## Total Hospital
df_total_hospital = df_imaging_total_volume_POS_prov_pos_rename_total_hospital.loc[df_imaging_total_volume_POS_prov_pos_rename_total_hospital["PlaceofService_Name"]=="Total Hospital"]

In [ ]:
### Subset 2018 to look at proportion of service by each provider within each Place of Service


In [40]:
df_ER_2018 = df_ER.loc[df_ER["year"]==2018]

df_inpatient_2018 = df_inpatient.loc[df_inpatient["year"]==2018]

df_HOPD_2018 = df_HOPD.loc[df_HOPD["year"]==2018]

df_office_2018 = df_office.loc[df_office["year"]==2018]

df_urgent_2018 = df_urgent.loc[df_urgent["year"]==2018]

df_total_hospital_2018 = df_total_hospital.loc[df_total_hospital["year"]==2018]

In [41]:
## Test for radiologists
df_office_2018_rads = df_office_2018.loc[df_office_2018["specialty"]=="Diagnostic radiology"]

total_service = np.sum(df_office_2018['psps_submitted_service_cnt'])
spec_service = np.sum(df_office_2018_rads['psps_submitted_service_cnt'])
service_prop = (spec_service / total_service) * 100

service_prop

18.027804889399597

In [42]:
## Function to calculate proportion of service by each provider, in each Place of Service
# def service_proportion(df, spec_list):
    
def service_spec(df, spec_list):

    df_group = df.loc[df["specialty"].isin(spec_list)]
    df_group.reset_index(drop=True, inplace=True)
    total_service = np.sum(df['psps_submitted_service_cnt'])
    spec_service = np.sum(df_group['psps_submitted_service_cnt'])

    service_prop = (spec_service / total_service) * 100
   
    return spec_service

def service_proportion(df, spec_list):

    df_group = df.loc[df["specialty"].isin(spec_list)]
    df_group.reset_index(drop=True, inplace=True)
    total_service = np.sum(df['psps_submitted_service_cnt'])
    spec_service = np.sum(df_group['psps_submitted_service_cnt'])

    service_prop = (spec_service / total_service) * 100
   
    return service_prop
  

In [43]:
service_proportion(df_office_2018, ['Diagnostic radiology'])

18.027804889399597

In [44]:
service_spec(df_office_2018, ['Diagnostic radiology'])

1610706.0

In [45]:
####################################
## EMERGENCY Breadown by Provider ##
####################################
rads_emergency_prop = service_proportion(df_ER_2018, ['Diagnostic radiology'])
ortho_emergency_prop = service_proportion(df_ER_2018, ['Orthopedic surgery'])
pa_emergency_prop = service_proportion(df_ER_2018, ['Physician assistant'])
pcp_emergency_prop = service_proportion(df_ER_2018, ['Primary Care'])
emergency_emergency_prop = service_proportion(df_ER_2018, ['Emergency medicine'])

emergency_prop = pd.DataFrame({'specialty':['Diagnostic radiology', 'Orthopedic surgery', 'Physician assistant', 'Primary Care', 'Emergency medicine'],'service_proportion':[rads_emergency_prop, ortho_emergency_prop, pa_emergency_prop, pcp_emergency_prop, emergency_emergency_prop]})
emergency_prop



specialty  service_proportion
0  Diagnostic radiology              96.950
1    Orthopedic surgery               0.002
2   Physician assistant               0.126
3          Primary Care               0.023
4    Emergency medicine               1.130

In [52]:
#################################
## OFFICE Breadown by Provider ##
#################################
rads_office_prop = service_proportion(df_office_2018, ['Diagnostic radiology'])
ortho_office_prop = service_proportion(df_office_2018, ['Orthopedic surgery'])
pa_office_prop = service_proportion(df_office_2018, ['Physician assistant'])
pcp_office_prop = service_proportion(df_office_2018, ['Primary Care'])
emergency_office_prop = service_proportion(df_office_2018, ['Emergency medicine'])

office_prop = pd.DataFrame({'specialty':['Diagnostic radiology', 'Orthopedic surgery', 'Physician assistant', 'Primary Care', 'Emergency medicine'],'service_proportion':[rads_office_prop, ortho_office_prop, pa_office_prop, pcp_office_prop, emergency_office_prop]})
office_prop


specialty  service_proportion
0  Diagnostic radiology              18.028
1    Orthopedic surgery              60.551
2   Physician assistant               8.552
3          Primary Care               1.046
4    Emergency medicine               0.259

In [ ]:
#################################
## OFFICE Breadown by Provider ##
#################################
rads_office_prop = (service_spec(df_office_2018, ['Diagnostic radiology']) / office_total) * 100
ortho_office_prop = (service_spec(df_office_2018, ['Orthopedic surgery']) / office_total) * 100
pa_office_prop = (service_spec(df_office_2018, ['Physician assistant']) / office_total) * 100
pcp_office_prop = (service_spec(df_office_2018, ['Primary Care']) / office_total) * 100
emergency_office_prop = (service_spec(df_office_2018, ['Emergency medicine']) / office_total) * 100

office_prop = pd.DataFrame({'specialty':['Diagnostic radiology', 'Orthopedic surgery', 'Physician assistant', 'Primary Care', 'Emergency medicine'],'service_proportion':[rads_office_prop, ortho_office_prop, pa_office_prop, pcp_office_prop, emergency_office_prop]})
office_prop

In [48]:
####################################
## INPATIENT Breadown by Provider ##
####################################
rads_inpatient_prop = (service_proportion(df_inpatient_2018, ['Diagnostic radiology'])) 
ortho_inpatient_prop = (service_proportion(df_inpatient_2018, ['Orthopedic surgery']))
pa_inpatient_prop = (service_proportion(df_inpatient_2018, ['Physician assistant']))
pcp_inpatient_prop = (service_proportion(df_inpatient_2018, ['Primary Care'])) 
emergency_inpatient_prop = (service_proportion(df_inpatient_2018, ['Emergency medicine']))

inpatient_prop = pd.DataFrame({'specialty':['Diagnostic radiology', 'Orthopedic surgery', 'Physician assistant', 'Primary Care', 'Emergency medicine'],'service_proportion':[rads_inpatient_prop, ortho_inpatient_prop, pa_inpatient_prop, pcp_inpatient_prop, emergency_inpatient_prop]})
inpatient_prop

specialty  service_proportion
0  Diagnostic radiology              97.683
1    Orthopedic surgery               0.558
2   Physician assistant               0.001
3          Primary Care               0.006
4    Emergency medicine               0.018

In [ ]:
####################################
## INPATIENT Breadown by Provider ##
####################################
rads_inpatient_prop = (service_spec(df_inpatient_2018, ['Diagnostic radiology']) / inpatient_total) * 100
ortho_inpatient_prop = (service_spec(df_inpatient_2018, ['Orthopedic surgery']) / inpatient_total) * 100
pa_inpatient_prop = (service_spec(df_inpatient_2018, ['Physician assistant']) / inpatient_total) * 100
pcp_inpatient_prop = (service_spec(df_inpatient_2018, ['Primary Care']) / inpatient_total) * 100
emergency_inpatient_prop = (service_spec(df_inpatient_2018, ['Emergency medicine']) / inpatient_total) * 100

inpatient_prop = pd.DataFrame({'specialty':['Diagnostic radiology', 'Orthopedic surgery', 'Physician assistant', 'Primary Care', 'Emergency medicine'],'service_proportion':[rads_inpatient_prop, ortho_inpatient_prop, pa_inpatient_prop, pcp_inpatient_prop, emergency_inpatient_prop]})
inpatient_prop

In [49]:
####################################
## OUTPATIENT Breadown by Provider ##
####################################
rads_outpatient_prop = (service_proportion(df_HOPD_2018, ['Diagnostic radiology']))
ortho_outpatient_prop = (service_proportion(df_HOPD_2018, ['Orthopedic surgery']))
pa_outpatient_prop = (service_proportion(df_HOPD_2018, ['Physician assistant']))
pcp_outpatient_prop = (service_proportion(df_HOPD_2018, ['Primary Care']))
emergency_outpatient_prop = (service_proportion(df_HOPD_2018, ['Emergency medicine']))

outpatient_prop = pd.DataFrame({'specialty':['Diagnostic radiology', 'Orthopedic surgery', 'Physician assistant', 'Primary Care', 'Emergency medicine'],'service_proportion':[rads_outpatient_prop, ortho_outpatient_prop, pa_outpatient_prop, pcp_outpatient_prop, emergency_outpatient_prop]})
outpatient_prop

specialty  service_proportion
0  Diagnostic radiology              91.293
1    Orthopedic surgery               5.494
2   Physician assistant               1.034
3          Primary Care               0.033
4    Emergency medicine               0.072

In [50]:
##########################################
## TOTAL HOSPITAL Breadown by Provider ##
##########################################
rads_totalHospital_prop = (service_proportion(df_total_hospital_2018, ['Diagnostic radiology']))
ortho_totalHospital_prop = (service_proportion(df_total_hospital_2018, ['Orthopedic surgery']))
pa_totalHospital_prop = (service_proportion(df_total_hospital_2018, ['Physician assistant']))
pcp_totalHospital_prop = (service_proportion(df_total_hospital_2018, ['Primary Care']))
emergency_totalHospital_prop = (service_proportion(df_total_hospital_2018, ['Emergency medicine']))

totalHospital_prop = pd.DataFrame({'specialty':['Diagnostic radiology', 'Orthopedic surgery', 'Physician assistant', 'Primary Care', 'Emergency medicine'],'service_proportion':[rads_totalHospital_prop, ortho_totalHospital_prop, pa_totalHospital_prop, pcp_totalHospital_prop, emergency_totalHospital_prop]})
totalHospital_prop

specialty  service_proportion
0  Diagnostic radiology              94.658
1    Orthopedic surgery               2.465
2   Physician assistant               0.492
3          Primary Care               0.024
4    Emergency medicine               0.468

In [51]:
##########################################
## URGENT CARE Breadown by Provider ##
##########################################
rads_urgent_prop = (service_proportion(df_urgent_2018, ['Diagnostic radiology']))
ortho_urgent_prop = (service_proportion(df_urgent_2018, ['Orthopedic surgery']))
pa_urgent_prop = (service_proportion(df_urgent_2018, ['Physician assistant']))
pcp_urgent_prop = (service_proportion(df_urgent_2018, ['Primary Care']))
emergency_urgent_prop = (service_proportion(df_urgent_2018, ['Emergency medicine']))

urgent_prop = pd.DataFrame({'specialty':['Diagnostic radiology', 'Orthopedic surgery', 'Physician assistant', 'Primary Care', 'Emergency medicine'],'service_proportion':[rads_urgent_prop, ortho_urgent_prop, pa_urgent_prop, pcp_urgent_prop, emergency_urgent_prop]})
urgent_prop

specialty  service_proportion
0  Diagnostic radiology              31.317
1    Orthopedic surgery               1.336
2   Physician assistant              28.023
3          Primary Care               5.328
4    Emergency medicine              15.688

In [ ]:
## Emergency Room Hospital
# df_ER_gr = df_ER.groupby(["year", "PlaceofService_Name"], as_index=False)["psps_submitted_service_cnt"].sum()
# df_ER_gr = df_ER_gr.merge(df_medicare_enrollment, on = "year", how="inner")
# df_ER_gr["utilization"] = df_ER_gr["psps_submitted_service_cnt"] / (df_ER_gr["Total_Original_Medicare_Enrollment"] / 1000)

# odf_ER_gr

In [ ]:
#####################
## END OF ANALYSIS ##
#####################

In [ ]:
## Hospital - Inpatient (HOPD)
df_inpatient_gr = df_inpatient.groupby(["year", "PlaceofService_Name"], as_index=False)["psps_submitted_service_cnt"].sum()
df_inpatient_gr = df_inpatient_gr.merge(df_medicare_enrollment, on = "year", how="inner")
df_inpatient_gr["utilization"] = df_inpatient_gr["psps_submitted_service_cnt"] / (df_inpatient_gr["Total_Original_Medicare_Enrollment"] / 1000)

df_inpatient_gr_perc = perc_change(df_inpatient_gr, ["Inpatient Hospital"], 2012)
df_inpatient_gr_perc

In [ ]:
## Hospital - Outpatient (HOPD)
df_HOPD_gr = df_HOPD.groupby(["year", "PlaceofService_Name"], as_index=False)["psps_submitted_service_cnt"].sum()
df_HOPD_gr = df_HOPD_gr.merge(df_medicare_enrollment, on = "year", how="inner")
df_HOPD_gr["utilization"] = df_HOPD_gr["psps_submitted_service_cnt"] / (df_HOPD_gr["Total_Original_Medicare_Enrollment"] / 1000)

df_HOPD_gr_perc = perc_change(df_HOPD_gr, ["HOPD"], 2012)
df_HOPD_gr_perc

In [ ]:
## Total Hospital (Inpatient, Outpatient, ED)
df_total_hospital_gr = df_total_hospital.groupby(["year", "PlaceofService_Name"], as_index=False)["psps_submitted_service_cnt"].sum()
df_total_hospital_gr = df_total_hospital_gr.merge(df_medicare_enrollment, on = "year", how="inner")
df_total_hospital_gr["utilization"] = df_total_hospital_gr["psps_submitted_service_cnt"] / (df_total_hospital_gr["Total_Original_Medicare_Enrollment"] / 1000)

df_total_hospital_gr_perc = perc_change(df_total_hospital_gr, ["Total Hospital"], 2012)
df_total_hospital_gr_perc

In [ ]:
## Office
df_office_gr = df_office.groupby(["year", "PlaceofService_Name"], as_index=False)["psps_submitted_service_cnt"].sum()
df_office_gr = df_office_gr.merge(df_medicare_enrollment, on = "year", how="inner")
df_office_gr["utilization"] = df_office_gr["psps_submitted_service_cnt"] / (df_office_gr["Total_Original_Medicare_Enrollment"] / 1000)

df_office_gr_perc = perc_change(df_office_gr, ["Office"], 2012)
df_office_gr_perc

In [ ]:
## Urgent Care
df_urgent_gr = df_urgent.groupby(["year", "PlaceofService_Name"], as_index=False)["psps_submitted_service_cnt"].sum()
df_urgent_gr = df_urgent_gr.merge(df_medicare_enrollment, on = "year", how="inner")
df_urgent_gr["utilization"] = df_urgent_gr["psps_submitted_service_cnt"] / (df_urgent_gr["Total_Original_Medicare_Enrollment"] / 1000)

df_urgent_gr_perc = perc_change(df_urgent_gr, ["Urgent Care Facility"], 2012)
df_urgent_gr_perc

In [ ]:
# Radiologists
df_imaging_total_volume_prov_rename_rad = df_imaging_total_volume_prov.copy()
df_imaging_total_volume_prov_rename_rad.replace("Diagnostic radiology", "Radiologist", inplace=True)
df_imaging_total_volume_prov_rad = perc_change(df_imaging_total_volume_prov_rename_rad, ["Radiologist"], 2012)
df_imaging_total_volume_prov_rad

In [ ]:
## Ortho
df_ortho = df_imaging_total_volume_POS_prov_pos.loc[df_imaging_total_volume_POS_prov_pos["specialty"]=="Orthopedic surgery"]
df_ortho.sort_values(by="psps_submitted_service_cnt", ascending=False, inplace=True)
df_ortho.head(10)